Copyright **`(c)`** 2023 Giovanni Squillero `<giovanni.squillero@polito.it>`  
[`https://github.com/squillero/computational-intelligence`](https://github.com/squillero/computational-intelligence)  
Free for personal or classroom use; see [`LICENSE.md`](https://github.com/squillero/computational-intelligence/blob/master/LICENSE.md) for details.  

# LAB9

Write a local-search algorithm (eg. an EA) able to solve the *Problem* instances 1, 2, 5, and 10 on a 1000-loci genomes, using a minimum number of fitness calls. That's all.

### Deadlines:

* Submission: Sunday, December 3 ([CET](https://www.timeanddate.com/time/zones/cet))
* Reviews: Sunday, December 10 ([CET](https://www.timeanddate.com/time/zones/cet))

Notes:

* Reviews will be assigned  on Monday, December 4
* You need to commit in order to be selected as a reviewer (ie. better to commit an empty work than not to commit)

In [41]:
from random import choices, randint, random, choice, sample, uniform
from copy import copy, deepcopy
import logging
from pprint import pprint, pformat
from collections import namedtuple
#import numpy as np

from dataclasses import dataclass

import lab9_lib

In [42]:
fitness = lab9_lib.make_problem(10)
for n in range(10):
    ind = choices([0, 1], k=50)
    print(f"{''.join(str(g) for g in ind)}: {fitness(ind):.2%}")

print(fitness.calls)

01011111110010010110000110110101000001000000000101: 9.36%
10101111100001010010100101010100110001001011001000: 7.33%
10011010100010010110001111001101010001010001111011: 15.33%
00011101101100001110111010010101100000010001011101: 7.34%
11010010100110110010110011101011000111000001000101: 7.33%
11101001111010111110110010111011010100001011100011: 9.11%
11110111101111011100111011001001110010001100110000: 9.11%
11111110101001001101100101110111011110111110101100: 19.13%
11111110000010000000111010111101010011100011011101: 15.33%
01111011000101100001010100011001001111000111100101: 9.11%
10


In [43]:
# Evolution parameter
POPULATION_SIZE = 50
OFFSPRING_SIZE = 10
MUTATION_PROBABILITY = 0.2
MUTATION_TRESHOLD = 0.2
TOURNAMENT_SIZE = 2
NUM_LOCI = 1000
NUM_ISLANDS = 100
MIGRANTS_EACH = 5
NUM_GENERATIONS = 500

In [44]:
@dataclass
class Individual:
    fitness: tuple
    genotype: list[float]

def select_parent(pop):
    pool = [choice(pop) for _ in range(TOURNAMENT_SIZE)]
    champion = max(pool, key=lambda i: i.fitness)
    return champion

#roulette 
def roulette_wheel_selection(population):
    fitness_values = [individual.fitness for individual in population]
    total_fitness = sum(fitness_values)

    # Calcola le probabilità di selezione basate sulla fitness normalizzata
    probabilities = [fitness / total_fitness for fitness in fitness_values]

    # Seleziona un individuo utilizzando la ruota della roulette
    selected_index = choices(range(len(population)), probabilities)[0]

    return population[selected_index]

#elitism
def elitism_selection(population):
    # Ordina la popolazione in base alla fitness in modo decrescente
    sorted_population = sorted(population, key=lambda x: x.fitness, reverse=True)

    # Estrai i primi 'elite_size' individui (l'élite)
    elite = sorted_population[0]

    return elite

#Selection functiion
def selection(population):
    selected_indices = sample(range(len(population)), 2)
    return [population[selected_indices[0]], population[selected_indices[1]]]

#mutation individual (:Individual   help to autocoplite code) (-> Individual   means that i return an Individual)
def mutate_one(ind: Individual) -> Individual: 
    offspring = deepcopy(ind)
    while True:
        #I select the two genomes to modify and cycle until they are equal
        while True:
            to_change_1 = randint(0, len(ind.genotype)-1)
            to_change_2 = randint(0, len(ind.genotype)-1)

            if(to_change_1 != to_change_2):
                break

        #controllo di non rimuovere la soglia da un valore che è gia a 0 o aggiungerla a un valore che è gia 1
        if offspring.genotype[to_change_1] - MUTATION_TRESHOLD >= 0 and offspring.genotype[to_change_2] + MUTATION_TRESHOLD <= 1:
            offspring.genotype[to_change_1] -= MUTATION_TRESHOLD
            offspring.genotype[to_change_2] += MUTATION_TRESHOLD
            break

    offspring.genotype = [round(element, 2) for element in offspring.genotype]
    return offspring

def mutate_add_one(ind: Individual) -> Individual:
    offspring = deepcopy(ind)

    # Probability to add 1 in a random position
    mutation_probability = 0.8

    for i in range(len(offspring.genotype)):
        if random() < mutation_probability:
            # add 1 in a random position
            offspring.genotype[i] = 1

    return offspring

def mutate_copy(ind: Individual) -> Individual:
    offspring = deepcopy(ind)

    # Select the position that i want to copy
    pos_to_copy = randint(0, NUM_LOCI-1)
    n = 10
    pos_to_start = randint(0, NUM_LOCI-1-n)

    for i in range(pos_to_start, pos_to_start + n):
        offspring.genotype[i] = ind.genotype[pos_to_copy]
    return offspring

#Mutation function
def mutate_two(individual):
    mutated_individual = [gene + uniform(-MUTATION_TRESHOLD, MUTATION_TRESHOLD) for gene in individual]
    return mutated_individual

#Migration function
def migrate(islands):
    for island in islands:
        migrants = [choice(island) for _ in range(MIGRANTS_EACH)]
        island.extend(migrants)

def one_cut_xover(ind1: Individual, ind2: Individual):
    cut_point = randint(1, NUM_LOCI-1)
    offspring_one = Individual(fitness=None,
                           genotype=ind1.genotype[:cut_point] + ind2.genotype[cut_point:])
    offspring_two = Individual(fitness=None,
                           genotype=ind2.genotype[:cut_point] + ind2.genotype[cut_point:])
    assert len(offspring_one.genotype) == NUM_LOCI
    assert len(offspring_two.genotype) == NUM_LOCI
    return offspring_one, offspring_two

def two_cut_xover(ind1: Individual, ind2: Individual):
    cut_point_one = randint(1, NUM_LOCI-2)
    #print(cut_point_one)
    cut_point_two = randint(cut_point_one + 1 , NUM_LOCI-1)
    #print(cut_point_two)

    offspring_one = Individual(fitness=None,
                           genotype= ind1.genotype[:cut_point_one] + ind2.genotype[cut_point_one:cut_point_two] + ind1.genotype[cut_point_two:])
    offspring_two = Individual(fitness=None,
                           genotype= ind2.genotype[:cut_point_one] + ind1.genotype[cut_point_one:cut_point_two] + ind2.genotype[cut_point_two:])
    assert len(offspring_one.genotype) == NUM_LOCI
    assert len(offspring_two.genotype) == NUM_LOCI
    return offspring_one, offspring_two

def three_cut_xover(ind1: Individual, ind2: Individual) -> (Individual, Individual):
    cut_point_one = randint(1, NUM_LOCI-3)
    #print(cut_point_one)
    cut_point_two = randint(cut_point_one + 1 , NUM_LOCI-2)
    #print(cut_point_two)
    cut_point_three = randint(cut_point_two + 1 , NUM_LOCI-1)
    #print(cut_point_three)

    offspring_one = Individual(fitness=None,
                           genotype= ind1.genotype[:cut_point_one] + ind2.genotype[cut_point_one:cut_point_two] + ind1.genotype[cut_point_two:cut_point_three] + ind2.genotype[cut_point_three:])
    offspring_two = Individual(fitness=None,
                           genotype= ind2.genotype[:cut_point_one] + ind1.genotype[cut_point_one:cut_point_two] + ind2.genotype[cut_point_two:cut_point_three] + ind1.genotype[cut_point_three:])
    assert len(offspring_one.genotype) == NUM_LOCI
    assert len(offspring_two.genotype) == NUM_LOCI
    return offspring_one, offspring_two

def uniform_xover(ind1: Individual, ind2: Individual):
    offspring_one = Individual(fitness = None, genotype = [])
    offspring_two = Individual(fitness = None, genotype = [])
    for _ in range(NUM_LOCI):
        i = random()
        if (i < 0.5):
            offspring_one.genotype.append(ind2.genotype[_])
            offspring_two.genotype.append(ind1.genotype[_])
        else:
            offspring_one.genotype.append(ind1.genotype[_])
            offspring_two.genotype.append(ind2.genotype[_])

    #assert len(offspring_one.genotype) == NUM
    #assert len(offspring_two.genotype) == NUM
    return offspring_one, offspring_two

mutations = [mutate_one, mutate_add_one, mutate_copy]
xovers = [one_cut_xover, two_cut_xover, three_cut_xover, uniform_xover]


In [45]:
islands = [
    [
        Individual(genotype=[choice((0, 1)) for _ in range(NUM_LOCI)], fitness=None)
        for _ in range(POPULATION_SIZE)
    ]
    for _ in range(NUM_ISLANDS)
]

for island in islands:
    for ind in island:
        ind.fitness = fitness(ind.genotype)

for generation in range(NUM_GENERATIONS):
    for island in islands:
        #offspring = []
        offspring = list()
        for counter in range(OFFSPRING_SIZE):
            if random() < MUTATION_PROBABILITY:  # self-adapt mutation probability
                # mutation  # add more clever mutations
                parent = roulette_wheel_selection(island)
                child = mutations[randint(0, len(mutations)-1)](parent)
            else:
                # xover # add more xovers
                parent1 = roulette_wheel_selection(island)
                parent2 = roulette_wheel_selection(island)
                
                child1, child2 = xovers[randint(0, len(xovers)-1)](parent1, parent2)
            offspring.append(child1)
            offspring.append(child2)

# calculate fitness of the selected genotypes
        for i in offspring:
            i.fitness = fitness(i.genotype)

        #do the migration
        migrate(islands)

        # Extend the population with new offspring and maintain the desired size
        island.extend(offspring)
        island.sort(key=lambda i: i.fitness, reverse=True)
        island[:] = island[:POPULATION_SIZE]

    # Print the fitness of the best individual on each island
    for i, island in enumerate(islands):
        print(f"Island {i+1}, Generation {generation+1}, Best Fitness: {island[0].fitness}, Fitness calls: {fitness.calls}")

    for i in offspring:
        i.fitness = fitness(i.genotype)
    island.extend(offspring)
    island.sort(key=lambda i: i.fitness, reverse=True)
    island = island[:POPULATION_SIZE]
    print(island[0].fitness)

Island 1, Generation 1, Best Fitness: 0.1620123795, Fitness calls: 7010
Island 2, Generation 1, Best Fitness: 0.15623570269999998, Fitness calls: 7010
Island 3, Generation 1, Best Fitness: 0.15044800179999998, Fitness calls: 7010
Island 4, Generation 1, Best Fitness: 0.1590044685, Fitness calls: 7010
Island 5, Generation 1, Best Fitness: 0.11225781119, Fitness calls: 7010
Island 6, Generation 1, Best Fitness: 0.11193778928, Fitness calls: 7010
Island 7, Generation 1, Best Fitness: 0.210122706, Fitness calls: 7010
Island 8, Generation 1, Best Fitness: 0.210122706, Fitness calls: 7010
Island 9, Generation 1, Best Fitness: 0.10611257031, Fitness calls: 7010
Island 10, Generation 1, Best Fitness: 0.11811249039999999, Fitness calls: 7010
Island 11, Generation 1, Best Fitness: 0.217936896, Fitness calls: 7010
Island 12, Generation 1, Best Fitness: 0.11581223696000001, Fitness calls: 7010
Island 13, Generation 1, Best Fitness: 0.16500235749999997, Fitness calls: 7010
Island 14, Generation 1, 